#### Create Final Table that will be sent to LLM Model

In [0]:
# Read the data from the intermediate table
df_investments_funding = spark.read.table("dev_db.intermediate.investments_funding")
df_active_companies = spark.read.table("dev_db.intermediate.active_companies")

In [0]:
# Get the latest date for each org_uuid
df_latest_raise = (
    df_investments_funding.groupBy("org_uuid")
    .agg({"announced_on": "max"})
    .withColumnRenamed("MAX(announced_on)", "latest_raise")
)

In [0]:
# Get the amount raised, investments for latest raise for each org_uuid
import pyspark.sql.functions as F

df_latest_funding = (
    df_latest_raise.alias("a")
    .join(
        df_investments_funding.alias("b"),
        (F.col("a.org_uuid") == F.col("b.org_uuid"))
        & (F.col("a.latest_raise") == F.col("b.announced_on")),
        "left",
    )
    .groupBy("a.org_uuid", "a.latest_raise")
    .agg(
        F.sum(F.col("b.raised_amount_usd")).alias("raised_amount"),
        F.array_join(F.collect_set(F.col("b.investments")), ", ").alias("investments"),
    )
)

In [0]:
from pyspark.sql.functions import col, concat_ws, lit

# Join Active companies to latest funding to get each company's latest funding
df_active_companies_latest = df_active_companies.join(
    df_latest_funding, on="org_uuid", how="left"
).select(
    col("org_uuid"),
    col("name"),
    col("org_type"),
    col("country_code"),
    col("homepage_url"),
    col("status"),
    col("description"),
    col("investments"),
    concat_ws(
        " ",
        col("description"),
        lit(" Website: "),
        col("homepage_url"),
        lit(" Headquarter: "),
        col("country_code"),
        lit(" Recent Investments: "),
        col("investments"),
        lit(" Amount Raised: "),
        col("raised_amount"),
        lit(" Date Announced: "),
        col("latest_raise"),
    ).alias("company_information"),
)

In [0]:
# Write the table to Unity Catalog.
df_active_companies_latest.write.format("delta").mode("overwrite").option("overwriteSchema", "true").saveAsTable("dev_db.core.active_companies_information")

In [0]:
%sql
select * from dev_db.core.active_companies_information

org_uuid name org_type country_code homepage_url status description investments company_information 8c57c3c2-e65b-e45b-c754-89dc9f85580a Gaia Online organization USA https://www.gaiaonline.com/ operating Gaia Online has grown into one of the biggest forum communities in the world. Today, Gaia is the best place on the web to discuss anime, games, comics, sci-fi, fantasy and anything else you can imagine. Plus, there are tons of other free features to keep Gaia members permanently amused. IVP investment in Series C - Gaia Online Gaia Online has grown into one of the biggest forum communities in the world. Today, Gaia is the best place on the web to discuss anime, games, comics, sci-fi, fantasy and anything else you can imagine. Plus, there are tons of other free features to keep Gaia members permanently amused. Website: https://www.gaiaonline.com/ Headquarter: USA Recent Investments: IVP investment in Series C - Gaia Online Amount Raised: 11000000 Date Announced: 2008-07-14 6d2fff57-32b5-f75c-9986-97539d1bf366 Viddler organization USA http://www.viddler.com operating Viddler has a long history of innovation in online video, developing patented new approaches, and transforming video from a passive viewing experience to an interactive, measurable, user-centered one. Backed by a powerful, secure content delivery network, Viddler delivers millions of videos for thousands of businesses around the world every day. Mobile technology is everywhere. To accommodate this, Viddler has developed far-reaching HTML5 video player technology—expanding the concept of “learn anywhere” interactivity between instructors and students or consultants and clients. We are focused on: our innovation, our interactive video player, and our strong customer service. Our player systems allow us to have people who truly understand the message of a learning video because we refuse to have a passive user viewing experience. Viddler has a long history of innovation in online video, developing patented new approaches, and transforming video from a passive viewing experience to an interactive, measurable, user-centered one. Backed by a powerful, secure content delivery network, Viddler delivers millions of videos for thousands of businesses around the world every day. Mobile technology is everywhere. To accommodate this, Viddler has developed far-reaching HTML5 video player technology—expanding the concept of “learn anywhere” interactivity between instructors and students or consultants and clients. We are focused on: our innovation, our interactive video player, and our strong customer service. Our player systems allow us to have people who truly understand the message of a learning video because we refuse to have a passive user viewing experience. Website: http://www.viddler.com Headquarter: USA Recent Investments: Amount Raised: 294638 Date Announced: 2012-04-06 0cf4f50a-b749-04be-589f-301dc97dc6b5 Music Intelligence Solutions organization USA https://uplaya.com operating Music Intelligence Solutions, Inc.,is a ''smart'' music discovery player. MIS is a global digital media corporation with offices in San Francisco, CA; Savannah, GA; and Barcelona, Spain. The Company uses patent-approved technology to enhance the consumer experience with digital content including music and video. Ecosystem partners and customers include major music labels, digital media companies, mobile services providers and web 2.0 Internet services companies such as social networks and online retail portals. The approaches used by MIS across all product lines incorporate decades of development by the original research and development team, which consisted of musicians as well as world-class PHD physicists and mathematicians. Music Intelligence Solutions, Inc.,is a ''smart'' music discovery player. MIS is a global digital media corporation with offices in San Francisco, CA; Savannah, GA; and Barcelona, Spain. The Company uses patent-approved technology to enhance the consumer experience with d